# Goal of this notebook

Develop a training loop for finetuning ASR models using TTS loss by recreating RL training found in RL4LMs/rl4lms/envs/text_generation/training_utils.py

```bash
conda activate speller
cd /home/s1785140/rlspeller
```

# automatic reloading magic

# imports

In [101]:
import torch
from typing import List, Dict, Tuple, Any
import hyperpyyaml
from tqdm import tqdm
from torchaudio.models.decoder import ctc_decoder
from torch.nn.functional import softmax
import random
from jiwer import cer
import numpy as np
import speechbrain as sb
from IPython.display import Audio

## check if gpu available

In [102]:
# print hostname to make sure we are on correct node
import socket
print(socket.gethostname())

levi.inf.ed.ac.uk


In [103]:
torch.cuda.is_available()

True

In [104]:
import os
os.getcwd()

'/disk/nfs/ostrom/s1785140/rlspeller'

# HPARAMS

In [105]:
hparams = {
    "softdtw_temp": 0.01,
    "softdtw_bandwidth": 120,
    "dist_func": "l1",
    "sentencepiece_model_path": "/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/0_char.model",
    'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain_subsampling1x.yaml',
    # 'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain_subsampling2x.yaml',
    # 'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain.yaml', # 4x subsampling
    'sample_rate': 16000,
}

# TOKENIZER

In [106]:
# load pretrained tokenizer used to tokenizer ASR training inputs 
import sentencepiece as spm 
spm_path = hparams["sentencepiece_model_path"]
sp = spm.SentencePieceProcessor()
sp.load(spm_path)
print(sp.vocab_size())

28


In [107]:
# test tokenizer
s = "hello world my name is jason"
# TODO pass string through text cleaners? 
encoded = sp.EncodeAsIds(s)
assert 0 not in encoded, "tried to encode an unknown character"
print(" ".join(str(idx) for idx in encoded))

1 10 2 12 12 4 1 17 4 9 12 11 1 16 20 1 6 5 16 2 1 7 8 1 26 5 8 4 6


In [108]:
sp.DecodeIds(encoded)

'hello world my name is jason'

# NEW! SIMPLE TOKENIZER

In [109]:
from speechbrain.tokenizers.SimpleTokenizer import SimpleTokenizer

In [110]:
tokenizer = SimpleTokenizer()

In [111]:
text = "hello my name is jason"
text = text.replace(' ', '|')
print(text)
ids = tokenizer.encode_as_ids(text)
ids

hello|my|name|is|jason


[9, 6, 13, 13, 16, 1, 14, 26, 1, 15, 2, 14, 6, 1, 10, 20, 1, 11, 2, 20, 16, 15]

In [112]:
tokenizer.decode_ids(ids)

'hello|my|name|is|jason'

## test simple tokenizer with probability distribution, and see if CTC decoder successfully generates n-best lists

In [113]:
# create empty array of correct dimensions
min_len, max_len = 50, 100
bsz = 4
lens = torch.randint(min_len, max_len, (bsz,))
vocab_size = len(tokenizer.vocab)

# randomly assign probaility distribution to each timestep

# try to decode

In [114]:
randn = torch.randn(bsz, max_len, vocab_size)

In [115]:
ctc_probs = softmax(randn, dim=1)
# ctc_probs

In [116]:
ctc_beamsearch_decoder_test = ctc_decoder(
    lexicon=None,
    # tokens="/home/s1785140/rlspeller/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/tokens.txt",
    tokens=tokenizer.vocab,
    nbest=2,
    blank_token='-',
    sil_token="|",
)

predicted_ids = ctc_beamsearch_decoder_test(ctc_probs, lens)

predicted_words = []
for i, hyps in enumerate(predicted_ids):
    for j, hyp in enumerate(hyps):
        words = tokenizer.decode_ids(hyp.tokens.tolist()).split(" ")
        tup = (f"sample {i+1}, hyp {j+1}/{len(hyps)}", words)
        predicted_words.append(tup)
        print(tup)

('sample 1, hyp 1/2', ['|ea|mhkgvfrvktzbgblmc|jpodawpx|vaeiyq|ytklndygvtseopmradcwqar|lzxjsvisfl|'])
('sample 1, hyp 2/2', ['|ea|mhkgvfrvktzbgblmc|jpodawpx|vaeiyq|ytkdndygvtseopmradcwqar|lzxjsvisfl|'])
('sample 2, hyp 1/2', ['|bcwlxhjrujrhv|jrfmtg|hsexuqgizeadcedco|gkalsfsmnbmhkcldswumgudysijcpayfahbg|'])
('sample 2, hyp 2/2', ['|bcwlxhqrujrhv|jrfmtg|hsexuqgizeadcedco|gkalsfsmnbmhkcldswumgudysijcpayfahbg|'])
('sample 3, hyp 1/2', ['|arbdhmhxeumiadoplnpifd|cqbomlkdzkzqmjxagcm|akhrojptvjwczwj|grnrntihashlmchkdy|'])
('sample 3, hyp 2/2', ['|arbdhmhxeumiadoplnpifd|cqbomlkdzkzqmjuagcm|akhrojptvjwczwj|grnrntihashlmchkdy|'])
('sample 4, hyp 1/2', ['|hipfkitlayp|jyxmpiw|s|xwbrxsjiroqimvhgslacaitmpjazdvhewjaxsbtzcfn|'])
('sample 4, hyp 2/2', ['|hipfkitlayr|jyxmpiw|s|xwbrxsjiroqimvhgslacaitmpjazdvhewjaxsbtzcfn|'])


# LOAD ASR (PRETRAINED)

In [117]:
from templates.speech_recognition_CharTokens_NoLM.ASR.train import ASR
from templates.speech_recognition_CharTokens_NoLM.ASR.train import dataio_prepare
from torch.utils.data import DataLoader
from speechbrain.dataio.dataloader import LoopedLoader

In [118]:
# Load hyperparameters file with command-line overrides
speechbrain_hparams_file = hparams['speechbrain_hparams_file']
with open(speechbrain_hparams_file) as f:
    speechbrain_hparams = hyperpyyaml.load_hyperpyyaml(f)

/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/rirs_noises.zip exists. Skipping download


In [119]:
speechbrain_hparams['save_folder']

'/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/ASR/results/CRDNN_CHAR_LJSpeech_halved_subsampling1x/2602/save'

In [120]:
# initialise trainer (we don't want to train, but model is tightly coupled with trainer)
asr_brain = ASR(
    modules=speechbrain_hparams["modules"],
    opt_class=speechbrain_hparams["opt_class"],
    hparams=speechbrain_hparams,
    checkpointer=speechbrain_hparams["checkpointer"],
)

def setup_asr_brain_for_infer(asr_brain):
    asr_brain.on_evaluate_start(min_key="WER") # We call the on_evaluate_start that will load the best model
    asr_brain.modules.eval() # We set the model to eval mode (remove dropout etc)

print("if on_evaluate_start() get runtime error, likely need to restart notebook kernel")
setup_asr_brain_for_infer(asr_brain)

if on_evaluate_start() get runtime error, likely need to restart notebook kernel


In [121]:
# create dataset and dataloader for inference
datasets = dataio_prepare(speechbrain_hparams)

test_set = datasets['test']

if not isinstance(test_set, DataLoader) or isinstance(test_set, LoopedLoader):
    test_loader_kwargs=speechbrain_hparams["test_dataloader_opts"]
    test_set = asr_brain.make_dataloader(
        test_set, stage=sb.Stage.TEST, **test_loader_kwargs
    )

In [122]:
# get vocab from tokenizer (needed for ctc decoding)
vocab_size = len(asr_brain.hparams.tokenizer)
vocab = []
for i in range(vocab_size):
    vocab.append(asr_brain.hparams.tokenizer.decode_ids([i]))
print(vocab)

# edit vocab to match default ctc decoder symbols for blank and silence
vocab[0] = '-'
vocab[1] = "|"

print(vocab)

[' ⁇ ', '', 'e', 't', 'o', 'a', 'n', 'i', 's', 'r', 'h', 'd', 'l', 'c', 'f', 'u', 'm', 'w', 'p', 'g', 'y', 'b', 'v', 'k', 'x', 'q', 'j', 'z']
['-', '|', 'e', 't', 'o', 'a', 'n', 'i', 's', 'r', 'h', 'd', 'l', 'c', 'f', 'u', 'm', 'w', 'p', 'g', 'y', 'b', 'v', 'k', 'x', 'q', 'j', 'z']


In [123]:
ctc_beamsearch_decoder = ctc_decoder(
    lexicon=None,
    # tokens="/home/s1785140/rlspeller/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/tokens.txt",
    tokens=vocab,
    nbest=100,
    blank_token='-',
    sil_token="|",
)

In [124]:
# generate transcriptions for all batches in test set
def transcribe_dataset(asr_brain, dataset, greedy=False, num_batches_to_transcribe=None):
    # Now we iterate over the dataset and we simply compute_forward and decode
    with torch.no_grad():
        transcripts = []
        for batch in tqdm(list(dataset)[:num_batches_to_transcribe], dynamic_ncols=True):
            orig_transcriptions = batch.words

            # Make sure that your compute_forward returns the predictions !!!
            # In the case of the template, when stage = TEST, a beam search is applied 
            # in compute_forward(). 
            predictions = asr_brain.compute_forward(batch, stage=sb.Stage.TEST)
            
            ctc_probs = predictions['ctc_logprobs'] # FOR DEBUG

            if greedy:
                predicted_ids = sb.decoders.ctc_greedy_decode(
                    predictions["ctc_logprobs"], asr_brain.feat_lens, blank_id=asr_brain.hparams.blank_index
                )
                predicted_words = [
                    asr_brain.tokenizer.decode_ids(ids).split(" ")
                    for ids in predicted_ids
                ]
            else:
                # get mel lens from wav len ratios since torch ctc decoder requires lens in frames
                batch_max_len = predictions["ctc_logprobs"].size(1)
                bsz = predictions["ctc_logprobs"].size(0)
                mel_lens = torch.zeros(bsz)
                for i, len_ratio in enumerate(asr_brain.feat_lens):
                    mel_lens[i] = int(torch.round(len_ratio * batch_max_len))
                
                predicted_ids = ctc_beamsearch_decoder(
                    predictions["ctc_logprobs"], lengths=mel_lens
                )

                predicted_words = []
                for i, (utt_id, orig_text, hyps) in enumerate(zip(batch.utt_id, orig_transcriptions, predicted_ids)):
                    print(f"\nsample {i+1} - ({utt_id}: '{orig_text}')")
                    sample_cers = []
                    for j, hyp in enumerate(hyps):
                        words = asr_brain.hparams.tokenizer.decode_ids(hyp.tokens.tolist()) # .split("|")
                        # words = tokenizer.decode_ids(hyp.tokens.tolist()) # .split("|")
                        hyp_cer = 100 * cer(orig_text, words)
                        sample_cers.append(hyp_cer)
                        print(f"\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'")
                        predicted_words.append((f"sample {i+1}, hyp {j+1}/{len(hyps)}", words))
                        
                    print(f"\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ===")

            transcripts.append(predicted_words)

    return transcripts, ctc_probs

# transcripts, ctc_probs = transcribe_dataset(asr_brain, test_set, greedy=False, num_batches_to_transcribe=1)

# LOAD WORD ALIGNED WAVS into dataset

In [125]:
# imitate CLAs
import sys
import argparse
import math
import glob
from tqdm import tqdm

In [126]:
# set these in yaml config!
train_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_train_wordtoken_annotation.json'
valid_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_valid_wordtoken_annotation.json'
test_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_test_wordtoken_annotation.json'

In [127]:
speechbrain_hparams['train_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_train_wordtoken_annotation.json'
speechbrain_hparams['valid_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_valid_wordtoken_annotation.json'
speechbrain_hparams['test_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_test_wordtoken_annotation.json'

In [128]:
def dataio_prepare(hparams):
    """This function prepares the datasets to be used in the brain class.
    It also defines the data processing pipeline through user-defined functions.


    Arguments
    ---------
    hparams : dict
        This dictionary is loaded from the `train.yaml` file, and it includes
        all the hyperparameters needed for dataset construction and loading.

    Returns
    -------
    datasets : dict
        Dictionary containing "train", "valid", and "test" keys that correspond
        to the DynamicItemDataset objects.
    """
    # Define audio pipeline. In this case, we simply read the path contained
    # in the variable wav with the audio reader.
    # wav path like: data/ljspeech_wavs_16khz_word_aligned/differs/differs__LJ001-0001__occ1__len8320.wav
    @sb.utils.data_pipeline.takes("wav")
    @sb.utils.data_pipeline.provides("sig", "wav_path", "utt_id")
    def audio_pipeline(wav_path):
        """Load the audio signal. This is done on the CPU in the `collate_fn`."""
        sig = sb.dataio.dataio.read_audio(wav_path)
        yield sig

        yield wav_path

        utt_id = wav_path.split("/")[-1].split(".")[0]
        yield utt_id

    @sb.utils.data_pipeline.takes("samples_to_graphemes_ratio")
    @sb.utils.data_pipeline.provides("samples_to_graphemes_ratio")
    def ratio_pipeline(samples_to_graphemes_ratio):
        yield samples_to_graphemes_ratio

    @sb.utils.data_pipeline.takes("length")
    @sb.utils.data_pipeline.provides("length")
    def length_pipeline(length):
        yield length

    @sb.utils.data_pipeline.takes("words")
    @sb.utils.data_pipeline.provides("words")
    def text_pipeline(words):
        """Processes the transcriptions to generate proper labels

        NB Make sure that you yield exactly what is defined above in @sb.utils.data_pipeline.provides()"""
        yield words

        # TODO also yield mel for calculating fastpitch softdtw loss

    # Define datasets from json data manifest file
    # Define datasets sorted by ascending lengths for efficiency
    datasets = {}
    data_info = {
        "train": hparams["train_annotation"],
        "valid": hparams["valid_annotation"],
        "test": hparams["test_annotation"],
    }

    for split in data_info:
        datasets[split] = sb.dataio.dataset.DynamicItemDataset.from_json(
            json_path=data_info[split],
            dynamic_items=[audio_pipeline, ratio_pipeline, length_pipeline, text_pipeline],
            output_keys=[
                "id",
                "sig",
                "wav_path",
                "utt_id",
                "samples_to_graphemes_ratio",
                "length",
                "words",
            ],
        )
        hparams[f"{split}_dataloader_opts"]["shuffle"] = True

    def print_dataset_lens(extra_str):
        for split in data_info:
            dataset_split = datasets[split]
            print(f"{split} dataset has {len(dataset_split)} samples", extra_str)

    print_dataset_lens("before any filtering")

    # Filter data for samples_to_graphemes_ratio that is either too small or too large
    key_min_value = {}
    if hparams["min_samples_to_graphemes_ratio"] is not None:
        key_min_value = {"samples_to_graphemes_ratio": hparams["min_samples_to_graphemes_ratio"]}

    key_max_value = {}
    if hparams["max_samples_to_graphemes_ratio"] is not None:
        key_max_value = {"samples_to_graphemes_ratio": hparams["max_samples_to_graphemes_ratio"]}

    for split in data_info:
        datasets[split] = datasets[split].filtered_sorted(
            key_min_value=key_min_value,
            key_max_value=key_max_value,
        )
    print_dataset_lens("after filtering by min and max samples to graphemes ratio")

    # Filter samples whos length is too short
    key_min_value = {}
    if hparams["min_length_seconds"] is not None:
        key_min_value = {"length": hparams["min_length_seconds"]}
    for split in data_info:
        datasets[split] = datasets[split].filtered_sorted(
            key_min_value=key_min_value,
        )
    print_dataset_lens("after filtering by minimum length")

    # Sorting training data with ascending order makes the code  much
    # faster  because we minimize zero-padding. In most of the cases, this
    # does not harm the performance.
    if hparams["sorting"] == "ascending":
        datasets["train"] = datasets["train"].filtered_sorted(sort_key="length")
        hparams["train_dataloader_opts"]["shuffle"] = False

    elif hparams["sorting"] == "descending":
        datasets["train"] = datasets["train"].filtered_sorted(
            sort_key="length", reverse=True
        )
        hparams["train_dataloader_opts"]["shuffle"] = False

    elif hparams["sorting"] == "random":
        hparams["train_dataloader_opts"]["shuffle"] = True
        pass

    else:
        raise NotImplementedError(
            "sorting must be random, ascending or descending"
        )
    
    return datasets

datasets = dataio_prepare(speechbrain_hparams)

train dataset has 11453 samples before any filtering
valid dataset has 415 samples before any filtering
test dataset has 414 samples before any filtering
train dataset has 10642 samples after filtering by min and max samples to graphemes ratio
valid dataset has 391 samples after filtering by min and max samples to graphemes ratio
test dataset has 384 samples after filtering by min and max samples to graphemes ratio
train dataset has 10622 samples after filtering by minimum length
valid dataset has 389 samples after filtering by minimum length
test dataset has 384 samples after filtering by minimum length


In [129]:
# convert from datasets to dataloaders
split2stage = {"train": sb.Stage.TRAIN, "valid": sb.Stage.VALID, "test": sb.Stage.TEST}
for split in ["train", "valid", "test"]:
    if not isinstance(datasets[split], DataLoader) or isinstance(datasets[split], LoopedLoader):
        dataloader_kwargs=speechbrain_hparams[f"{split}_dataloader_opts"]
        datasets[split] = asr_brain.make_dataloader(
            datasets[split], stage=split2stage[split], **dataloader_kwargs
        )

In [130]:
def set_whitespace_to_0_probability(ctc_probs, vocab, log_probs=True, whitespace_symbol="|"):
    """ctc_probs [bsz, max_seq_len, vocab_size]"""
    new_probability = -math.inf if log_probs else 0.0
    ctc_probs[:,:,vocab.index(whitespace_symbol)] = new_probability
    return ctc_probs

# TRANSCRIBE WORD ALIGNED WAVS

In [131]:
# generate transcriptions for all batches in test set
def transcribe_dataset(asr_brain, dataset, 
                       num_batches_to_transcribe=None,
                       hack_whitespace_probs=False, collapse_whitespace=True,
                       print_info=False, max_hyps_per_sample=None):
    # Now we iterate over the dataset and we simply compute_forward and decode

    orig_words = []
    printouts = []
    orig_wavs = []
    n = 0 # number of batches transcribed

    with torch.no_grad():
        for batch in tqdm(dataset, dynamic_ncols=True, total=num_batches_to_transcribe):
            # break out of loop if we have transcribed enough batches
            if n >= num_batches_to_transcribe:
                break
            n += 1

            orig_transcriptions = batch.words
            wavs = batch.sig.data

            # Make sure that your compute_forward returns the predictions !!!
            # In the case of the template, when stage = TEST, a beam search is applied 
            # in compute_forward(). 
            predictions = asr_brain.compute_forward(batch, stage=sb.Stage.TEST)
            ctc_probs = predictions['ctc_logprobs'] # FOR DEBUG

            # hack probabilities to set all probs to 0 for whitespace
            if hack_whitespace_probs:
                ctc_probs = set_whitespace_to_0_probability(ctc_probs, vocab, log_probs=True, whitespace_symbol="|")

            # get mel lens from wav len ratios since torch ctc decoder requires lens in frames
            batch_max_len = predictions["ctc_logprobs"].size(1)
            bsz = predictions["ctc_logprobs"].size(0)
            mel_lens = torch.zeros(bsz)
            for i, len_ratio in enumerate(asr_brain.feat_lens):
                mel_lens[i] = int(torch.round(len_ratio * batch_max_len))
            
            predicted_ids = ctc_beamsearch_decoder(
                predictions["ctc_logprobs"], lengths=mel_lens
            )

            # iterate over samples in batch
            for i, (utt_id, orig_text, hyps, wav) in enumerate(zip(batch.utt_id, orig_transcriptions, predicted_ids, wavs)):
                sample_printout = f"\nsample {i+1} - ({utt_id}: '{orig_text}')"
                # if print_info: print(f"\nsample {i+1} - ({utt_id}: '{orig_text}')")
                sample_cers = []
                for j, hyp in enumerate(list(hyps)[:max_hyps_per_sample]):
                    words = asr_brain.hparams.tokenizer.decode_ids(hyp.tokens.tolist())
                    if collapse_whitespace:
                        words = "".join(c for c in words if c != " ")
                    hyp_cer = 100 * cer(orig_text, words)
                    sample_cers.append(hyp_cer)
                    sample_printout += f"\n\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'"
                    # if print_info: print(f"\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'")
                    
                sample_printout += f"\n\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ==="
                # if print_info: print(f"\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ===")

                orig_words.append(orig_text)
                printouts.append(sample_printout)
                orig_wavs.append(wav)

    output_dict = {
        "words": orig_words,
        "wavs": orig_wavs,
        "printouts": printouts,
    }

    return output_dict

NUM_BATCHES_TO_TRANSCRIBE = 5
MAX_HYPS_PER_SAMPLE = 20
transcription_output_dict_no_hack = transcribe_dataset(asr_brain, datasets["train"], 
                                               num_batches_to_transcribe=NUM_BATCHES_TO_TRANSCRIBE,
                                               collapse_whitespace=False,
                                               max_hyps_per_sample=MAX_HYPS_PER_SAMPLE)

transcription_output_dict_hack = transcribe_dataset(asr_brain, datasets["train"], 
                                               num_batches_to_transcribe=NUM_BATCHES_TO_TRANSCRIBE,
                                               collapse_whitespace=False, hack_whitespace_probs=True,
                                               max_hyps_per_sample=MAX_HYPS_PER_SAMPLE)

100%|███████████████████████████████████████████████████████| 5/5 [00:38<00:00,  7.77s/it]


In [132]:
for printout1, printout2, wav in zip(transcription_output_dict_no_hack["printouts"], 
                         transcription_output_dict_hack["printouts"], 
                         transcription_output_dict_no_hack["wavs"]):
    print('NO HACK', printout1)
    print('HACK', printout2)
    display(Audio(wav, rate=16000))

NO HACK 
sample 1 - (unconstitutionality__LJ021-0191__occ1__len25760: 'unconstitutionality')
	hyp 1/50 (CER=5.3%): 'un constitutionality '
	hyp 2/50 (CER=10.5%): 'un constitutionaloity '
	hyp 3/50 (CER=10.5%): 'cun constitutionality '
	hyp 4/50 (CER=5.3%): 'un constitutionality '
	hyp 5/50 (CER=10.5%): 'on constitutionality '
	hyp 6/50 (CER=10.5%): 'un constitutionaloty '
	hyp 7/50 (CER=0.0%): 'unconstitutionality '
	hyp 8/50 (CER=10.5%): 'un constitution ality '
	hyp 9/50 (CER=10.5%): 'hun constitutionality '
	hyp 10/50 (CER=10.5%): 'tun constitutionality '
	hyp 11/50 (CER=10.5%): 'gun constitutionality '
	hyp 12/50 (CER=10.5%): 'mun constitutionality '
	hyp 13/50 (CER=15.8%): 'cun constitutionaloity '
	hyp 14/50 (CER=10.5%): 'fun constitutionality '
	hyp 15/50 (CER=10.5%): 'nun constitutionality '
	hyp 16/50 (CER=10.5%): 'un constitutionhality '
	hyp 17/50 (CER=10.5%): 'un constitutionalioty '
	hyp 18/50 (CER=10.5%): 'un constitutionaleity '
	hyp 19/50 (CER=10.5%): 'un constitutional

NO HACK 
sample 2 - (anesthesiologists__LJ031-0023__occ1__len24000: 'anesthesiologists')
	hyp 1/50 (CER=29.4%): 'an as theasyologists '
	hyp 2/50 (CER=29.4%): 'an as theaseologists '
	hyp 3/50 (CER=23.5%): 'anas theasyologists '
	hyp 4/50 (CER=29.4%): 'an is theasyologists '
	hyp 5/50 (CER=29.4%): 'an as heasyologists '
	hyp 6/50 (CER=23.5%): 'anas theaseologists '
	hyp 7/50 (CER=29.4%): 'an is theaseologists '
	hyp 8/50 (CER=29.4%): 'an as heaseologists '
	hyp 9/50 (CER=23.5%): 'an as thesyologists '
	hyp 10/50 (CER=23.5%): 'anis theasyologists '
	hyp 11/50 (CER=35.3%): 'an as theasyologests '
	hyp 12/50 (CER=23.5%): 'anas heasyologists '
	hyp 13/50 (CER=35.3%): 'an as teasyologists '
	hyp 14/50 (CER=29.4%): 'an is heasyologists '
	hyp 15/50 (CER=23.5%): 'an as theseologists '
	hyp 16/50 (CER=23.5%): 'an es theasyologists '
	hyp 17/50 (CER=23.5%): 'anis theaseologists '
	hyp 18/50 (CER=35.3%): 'an as theaseologests '
	hyp 19/50 (CER=23.5%): 'anas heaseologists '
	hyp 20/50 (CER=35.3%)

NO HACK 
sample 3 - (misrepresentations__LJ005-0034__occ1__len23200: 'misrepresentations')
	hyp 1/49 (CER=16.7%): 'misrepras untations '
	hyp 2/49 (CER=11.1%): 'misrepras entations '
	hyp 3/49 (CER=16.7%): 'misreprs untations '
	hyp 4/49 (CER=22.2%): 'mis repras untations '
	hyp 5/49 (CER=11.1%): 'misreprs entations '
	hyp 6/49 (CER=16.7%): 'mis repras entations '
	hyp 7/49 (CER=16.7%): 'misrepris untations '
	hyp 8/49 (CER=22.2%): 'mis reprs untations '
	hyp 9/49 (CER=22.2%): 'misreperas untations '
	hyp 10/49 (CER=16.7%): 'misrepras ontations '
	hyp 11/49 (CER=11.1%): 'misreprasuntations '
	hyp 12/49 (CER=22.2%): 'misreporas untations '
	hyp 13/49 (CER=11.1%): 'misrepris entations '
	hyp 14/49 (CER=11.1%): 'misrepres untations '
	hyp 15/49 (CER=22.2%): 'misreparas untations '
	hyp 16/49 (CER=16.7%): 'mis reprs entations '
	hyp 17/49 (CER=22.2%): 'misrebpras untations '
	hyp 18/49 (CER=22.2%): 'missrepras untations '
	hyp 19/49 (CER=16.7%): 'misreperas entations '
	hyp 20/49 (CER=5.6%

NO HACK 
sample 4 - (institutionalized__LJ040-0144__occ1__len21760: 'institutionalized')
	hyp 1/46 (CER=0.0%): 'institutionalized '
	hyp 2/46 (CER=5.9%): 'einstitutionalized '
	hyp 3/46 (CER=5.9%): 'hinstitutionalized '
	hyp 4/46 (CER=11.8%): 'heinstitutionalized '
	hyp 5/46 (CER=5.9%): 'nstitutionalized '
	hyp 6/46 (CER=0.0%): 'institutionalized '
	hyp 7/46 (CER=5.9%): 'enstitutionalized '
	hyp 8/46 (CER=11.8%): 'e institutionalized '
	hyp 9/46 (CER=5.9%): 'hnstitutionalized '
	hyp 10/46 (CER=11.8%): 'h institutionalized '
	hyp 11/46 (CER=11.8%): 'henstitutionalized '
	hyp 12/46 (CER=17.6%): 'he institutionalized '
	hyp 13/46 (CER=5.9%): 'nstitutionalized '
	hyp 14/46 (CER=11.8%): 'e nstitutionalized '
	hyp 15/46 (CER=5.9%): 'ainstitutionalized '
	hyp 16/46 (CER=11.8%): 'h nstitutionalized '
	hyp 17/46 (CER=17.6%): 'he nstitutionalized '
	hyp 18/46 (CER=11.8%): 'hainstitutionalized '
	hyp 19/46 (CER=5.9%): 'institutionalised '
	hyp 20/46 (CER=5.9%): 'einstitutionalized '
	=== Mean CER

NO HACK 
sample 5 - (specifications__LJ043-0092__occ1__len21600: 'specifications')
	hyp 1/49 (CER=0.0%): 'specifications '
	hyp 2/49 (CER=7.1%): 'spescifications '
	hyp 3/49 (CER=7.1%): 'speciffications '
	hyp 4/49 (CER=7.1%): 'speccifications '
	hyp 5/49 (CER=0.0%): 'specifications '
	hyp 6/49 (CER=0.0%): 'specifications '
	hyp 7/49 (CER=7.1%): 'specsifications '
	hyp 8/49 (CER=7.1%): 'specifocations '
	hyp 9/49 (CER=7.1%): 'specification s '
	hyp 10/49 (CER=7.1%): 'spetcifications '
	hyp 11/49 (CER=7.1%): 'specificcations '
	hyp 12/49 (CER=7.1%): 'sppecifications '
	hyp 13/49 (CER=7.1%): 'speecifications '
	hyp 14/49 (CER=7.1%): 'spectifications '
	hyp 15/49 (CER=7.1%): 'spefcifications '
	hyp 16/49 (CER=7.1%): 'pecifications '
	hyp 17/49 (CER=7.1%): 'xspecifications '
	hyp 18/49 (CER=7.1%): 'specificationns '
	hyp 19/49 (CER=7.1%): 'specfifications '
	hyp 20/49 (CER=14.3%): 'spesciffications '
	=== Mean CER: 6.4%, Std CER: 3.1% ===
HACK 
sample 5 - (specifications__LJ043-0092__occ1_

...

NO HACK 
sample 16 - (situations__LJ050-0246__occ1__len17600: 'situations')
	hyp 1/46 (CER=0.0%): 'situations '
	hyp 2/46 (CER=20.0%): 'a situations '
	hyp 3/46 (CER=20.0%): 's situations '
	hyp 4/46 (CER=20.0%): 'f situations '
	hyp 5/46 (CER=20.0%): 'e situations '
	hyp 6/46 (CER=20.0%): 'o situations '
	hyp 7/46 (CER=20.0%): 't situations '
	hyp 8/46 (CER=20.0%): 'h situations '
	hyp 9/46 (CER=20.0%): 'r situations '
	hyp 10/46 (CER=20.0%): 'c situations '
	hyp 11/46 (CER=10.0%): 'situgations '
	hyp 12/46 (CER=0.0%): 'situations '
	hyp 13/46 (CER=10.0%): 'situuations '
	hyp 14/46 (CER=20.0%): 'd situations '
	hyp 15/46 (CER=20.0%): 'w situations '
	hyp 16/46 (CER=20.0%): 'g situations '
	hyp 17/46 (CER=20.0%): 'l situations '
	hyp 18/46 (CER=20.0%): 'u situations '
	hyp 19/46 (CER=20.0%): 'q situations '
	hyp 20/46 (CER=20.0%): 'p situations '
	=== Mean CER: 17.0%, Std CER: 6.4% ===
HACK 
sample 16 - (situations__LJ050-0246__occ1__len17600: 'situations')
	hyp 1/46 (CER=0.0%): 'situa

NO HACK 
sample 17 - (impossibility__LJ003-0343__occ1__len17600: 'impossibility')
	hyp 1/45 (CER=0.0%): 'impossibility  '
	hyp 2/45 (CER=0.0%): 'impossibility '
	hyp 3/45 (CER=7.7%): 'im possibility  '
	hyp 4/45 (CER=0.0%): 'impossibility  '
	hyp 5/45 (CER=7.7%): 'im possibility '
	hyp 6/45 (CER=15.4%): 'impossibility e '
	hyp 7/45 (CER=15.4%): 'impossibility i '
	hyp 8/45 (CER=7.7%): 'im possibility  '
	hyp 9/45 (CER=15.4%): 'impossibility o '
	hyp 10/45 (CER=15.4%): 'impossibility h '
	hyp 11/45 (CER=7.7%): 'impossibilitye '
	hyp 12/45 (CER=15.4%): 'impossibility t '
	hyp 13/45 (CER=7.7%): 'impossibilityi '
	hyp 14/45 (CER=15.4%): 'impossibility a '
	hyp 15/45 (CER=23.1%): 'im possibility e '
	hyp 16/45 (CER=15.4%): 'impossibility d '
	hyp 17/45 (CER=7.7%): 'impossibilityo '
	hyp 18/45 (CER=15.4%): 'impossibility w '
	hyp 19/45 (CER=7.7%): 'impossibilityh '
	hyp 20/45 (CER=23.1%): 'impossibility  e '
	=== Mean CER: 11.2%, Std CER: 6.7% ===
HACK 
sample 17 - (impossibility__LJ003-0343

NO HACK 
sample 18 - (allowances__LJ003-0292__occ1__len17600: 'allowances')
	hyp 1/49 (CER=0.0%): 'allowances '
	hyp 2/49 (CER=10.0%): 'alowances '
	hyp 3/49 (CER=10.0%): 'allowancis '
	hyp 4/49 (CER=10.0%): 'alllowances '
	hyp 5/49 (CER=20.0%): 'alowancis '
	hyp 6/49 (CER=10.0%): 'alloweances '
	hyp 7/49 (CER=10.0%): 'allowancs '
	hyp 8/49 (CER=20.0%): 'aloweances '
	hyp 9/49 (CER=10.0%): 'allowance '
	hyp 10/49 (CER=20.0%): 'alowancs '
	hyp 11/49 (CER=10.0%): 'ellowances '
	hyp 12/49 (CER=10.0%): 'allhowances '
	hyp 13/49 (CER=10.0%): 'allowanc es '
	hyp 14/49 (CER=20.0%): 'alowance '
	hyp 15/49 (CER=20.0%): 'alllowancis '
	hyp 16/49 (CER=10.0%): 'allowaences '
	hyp 17/49 (CER=20.0%): 'elowances '
	hyp 18/49 (CER=10.0%): 'alhowances '
	hyp 19/49 (CER=20.0%): 'alowanc es '
	hyp 20/49 (CER=10.0%): 'al lowances '
	=== Mean CER: 13.0%, Std CER: 5.6% ===
HACK 
sample 18 - (allowances__LJ003-0292__occ1__len17600: 'allowances')
	hyp 1/48 (CER=0.0%): 'allowances '
	hyp 2/48 (CER=10.0%): 'alo

NO HACK 
sample 19 - (disturbances__LJ004-0235__occ1__len17600: 'disturbances')
	hyp 1/50 (CER=25.0%): 'distermanses '
	hyp 2/50 (CER=16.7%): 'disterbanses '
	hyp 3/50 (CER=16.7%): 'disturmanses '
	hyp 4/50 (CER=8.3%): 'disturbanses '
	hyp 5/50 (CER=16.7%): 'distermances '
	hyp 6/50 (CER=8.3%): 'disterbances '
	hyp 7/50 (CER=8.3%): 'disturmances '
	hyp 8/50 (CER=0.0%): 'disturbances '
	hyp 9/50 (CER=25.0%): 'distervanses '
	hyp 10/50 (CER=16.7%): 'disturvanses '
	hyp 11/50 (CER=16.7%): 'distervances '
	hyp 12/50 (CER=8.3%): 'disturvances '
	hyp 13/50 (CER=25.0%): 'distermbanses '
	hyp 14/50 (CER=16.7%): 'disturmbanses '
	hyp 15/50 (CER=25.0%): 'disterbmanses '
	hyp 16/50 (CER=16.7%): 'distermbances '
	hyp 17/50 (CER=25.0%): 'disteranses '
	hyp 18/50 (CER=33.3%): 'distermenses '
	hyp 19/50 (CER=16.7%): 'disturbmanses '
	hyp 20/50 (CER=8.3%): 'disturmbances '
	=== Mean CER: 16.7%, Std CER: 7.9% ===
HACK 
sample 19 - (disturbances__LJ004-0235__occ1__len17600: 'disturbances')
	hyp 1/50 (CE

NO HACK 
sample 20 - (utilitarian__LJ001-0115__occ1__len17600: 'utilitarian')
	hyp 1/50 (CER=90.9%): 'the yutilletari im '
	hyp 2/50 (CER=81.8%): 'the yutilletariim '
	hyp 3/50 (CER=81.8%): 'the yutilletari am '
	hyp 4/50 (CER=100.0%): 'the yu tilletari im '
	hyp 5/50 (CER=72.7%): 'the yutilletariam '
	hyp 6/50 (CER=81.8%): 'the yutillitari im '
	hyp 7/50 (CER=90.9%): 'the yu tilletariim '
	hyp 8/50 (CER=72.7%): 'the yutillitariim '
	hyp 9/50 (CER=100.0%): 'the yutilletary im '
	hyp 10/50 (CER=81.8%): 'he yutilletari im '
	hyp 11/50 (CER=90.9%): 'the yu tilletari am '
	hyp 12/50 (CER=90.9%): 'the yutilletaryim '
	hyp 13/50 (CER=72.7%): 'the yutillitari am '
	hyp 14/50 (CER=72.7%): 'he yutilletariim '
	hyp 15/50 (CER=81.8%): 'the yu tilletariam '
	hyp 16/50 (CER=90.9%): 'the yu tillitari im '
	hyp 17/50 (CER=63.6%): 'the yutillitariam '
	hyp 18/50 (CER=100.0%): 'the yutillletari im '
	hyp 19/50 (CER=81.8%): 'the yu tillitariim '
	hyp 20/50 (CER=90.9%): 'the yutillletariim '
	=== Mean CE

In [133]:
# # display printouts and create audio player for each sample
# for printout, wav in zip(transcription_output_dict["printouts"], transcription_output_dict["wavs"]):
#     print(printout)
#     display(Audio(wav, rate=16000))